In [3]:
import pandas as pd

from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler

from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Input, Dense, Dropout
from tensorflow.keras.regularizers import l1, l2
from tensorflow.keras.optimizers import SGD

from scikeras.wrappers import KerasClassifier
from sklearn.model_selection import GridSearchCV, KFold

# add confusion matrix, f1 + auc score, precision/recall + roc curves

In [4]:
data = pd.read_csv('../Data/clean_df_engineering.csv')
data.drop(['Course'], axis=1, inplace=True)

data.head()

Age  Gender  CGPA  Stress_Level  Depression_Score  Anxiety_Score  \
0   24       0  2.44             0                 3              0   
1   22       0  3.62             3                 2              1   
2   22       0  3.16             2                 1              5   
3   25       0  3.48             2                 3              2   
4   23       0  3.65             2                 5              1   

   Sleep_Quality  Physical_Activity  Diet_Quality  Social_Support  \
0            0.5                0.0           0.5             0.0   
1            0.5                1.0           0.5             0.5   
2            1.0                0.0           0.5             0.5   
3            0.5                0.0           0.0             1.0   
4            1.0                0.5           0.5             0.0   

   Relationship_Status  Substance_Use  Counseling_Service_Use  Family_History  \
0                  0.0            0.5                     0.5               0   
1                  0.0            0.0                     1.0               1   
2                  0.0            0.0                     0.0               0   
3                  0.0            0.0                     0.5               0   
4                  0.0            0.0                     0.0               1   

   Chronic_Illness  Financial_Stress  Extracurricular_Involvement  \
0                0                 3                          0.0   
1                0                 5                          0.0   
2                0                 3                          0.0   
3                0                 2                          0.5   
4                0                 0                          0.5   

   Semester_Credit_Load  Residence_Type  
0                    27             0.0  
1                    24             0.0  
2                    21             0.0  
3                    29             1.0  
4                    19             1.0

In [5]:
features = ['Age', 'CGPA', 'Semester_Credit_Load', 'Anxiety_Score']
N_FEATURES = len(features)

In [6]:
BINARY_CLASSIFICATION = True
BINARY_ENCODE_THRESHOLD = 3 # values greater than this will be encoded as 1

# for multi-class classification:
N_CLASSES = len(data['Depression_Score'].unique())

In [7]:
# Define build_model function for KerasClassifier
# def build_model(num_layers, num_neurons, activation, dropout_rate, momentum, reg_method, reg_rate, learning_rate):
def build_model(num_layers, num_neurons, activation, momentum, reg_method, reg_rate, learning_rate):
    regularizer = l1(reg_rate) if reg_method=='l1' else l2(reg_rate)

    model = Sequential()

    # Input layer
    model.add(Input((N_FEATURES,)))
    # Hidden layers
    for _ in range(num_layers):
        model.add(Dense(num_neurons, activation=activation, kernel_regularizer=regularizer))
        # model.add(Dropout(dropout_rate))
    # Output layer
    if BINARY_CLASSIFICATION:
        model.add(Dense(1, activation='sigmoid')) # binary classification
    else:
        model.add(Dense(N_CLASSES, activation='softmax')) # multi-class classification

    optimizer = SGD(learning_rate=learning_rate, momentum=momentum)
    loss_string = 'binary_crossentropy' if BINARY_CLASSIFICATION else 'sparse_categorical_crossentropy'
    model.compile(loss=loss_string, optimizer=optimizer, metrics=['accuracy'])
    return model

## engineering dataset

In [6]:
# Load dataset
X = data[features]

if BINARY_CLASSIFICATION:
    y = data['Depression_Score'].apply(lambda x: 1 if x > BINARY_ENCODE_THRESHOLD else 0)
else:
    y = data['Depression_Score']

# Split data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=12, shuffle=True)

# Preprocess data
scaler = MinMaxScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

# Define parameters grid for grid search
param_grid = {
    # parameters for Sequential model
    'model__num_layers': [2, 3], # number of hidden layers
    'model__num_neurons': [32, 64],
    'model__dropout_rate': [0.2, 0.5],
    'model__momentum': [0.5, 0.9],
    'model__activation': ['relu', 'tanh'],
    'model__reg_method': ['l1', 'l2'],
    'model__reg_rate': [0.001, 0.01, 0.1],
    'model__learning_rate': [0.001, 0.01, 0.1],
    # parameters for KerasClassifier
    'batch_size': [32, 64]
}

# Create KerasClassifier wrapper for scikit-learn
model = KerasClassifier(build_fn=build_model, epochs=10, verbose=1)

# Perform grid search with cross-validation
kfold = KFold(n_splits=5, shuffle=True, random_state=42)

grid_search = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=-1, cv=kfold, scoring='accuracy')
grid_result = grid_search.fit(X_train, y_train)

c:\repos\ECS171FQ24_ResearchProject_SATAK\.venv\Lib\site-packages\joblib\externals\loky\process_executor.py:752: UserWarning: A worker stopped while some jobs were given to the executor. This can be caused by a too short worker timeout or by a memory leak.
  warnings.warn(
c:\repos\ECS171FQ24_ResearchProject_SATAK\.venv\Lib\site-packages\numpy\ma\core.py:2846: RuntimeWarning: invalid value encountered in cast
  _data = np.array(data, dtype=dtype, copy=copy,
c:\repos\ECS171FQ24_ResearchProject_SATAK\.venv\Lib\site-packages\scikeras\wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)


Epoch 1/10
12/12 ━━━━━━━━━━━━━━━━━━━━ 1s 3ms/step - accuracy: 0.6940 - loss: 1.3467  
Epoch 2/10
12/12 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - accuracy: 0.7173 - loss: 1.3377 
Epoch 3/10
12/12 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - accuracy: 0.7403 - loss: 1.3352 
Epoch 4/10
12/12 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.7330 - loss: 1.3323 
Epoch 5/10
12/12 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - accuracy: 0.7682 - loss: 1.3276 
Epoch 6/10
12/12 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - accuracy: 0.7964 - loss: 1.3121 
Epoch 7/10
12/12 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - accuracy: 0.7693 - loss: 1.3094 
Epoch 8/10
12/12 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - accuracy: 0.7753 - loss: 1.3086 
Epoch 9/10
12/12 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.7846 - loss: 1.3040 
Epoch 10/10
12/12 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - accuracy: 0.7733 - loss: 1.3053 


In [7]:
# Print results
print("Best: %f using %s" % (grid_result.best_score_, grid_result.best_params_))
means = grid_result.cv_results_['mean_test_score']
stds = grid_result.cv_results_['std_test_score']
params = grid_result.cv_results_['params']
for mean, std, param in zip(means, stds, params):
    print("%f (%f) with: %r" % (mean, std, param))

Best: 0.809709 using {'batch_size': 64, 'model__activation': 'relu', 'model__dropout_rate': 0.5, 'model__learning_rate': 0.001, 'model__momentum': 0.5, 'model__num_layers': 2, 'model__num_neurons': 64, 'model__reg_method': 'l2', 'model__reg_rate': 0.01}
0.808367 (0.024431) with: {'batch_size': 32, 'model__activation': 'relu', 'model__dropout_rate': 0.2, 'model__learning_rate': 0.001, 'model__momentum': 0.5, 'model__num_layers': 2, 'model__num_neurons': 32, 'model__reg_method': 'l1', 'model__reg_rate': 0.001}
0.808367 (0.024431) with: {'batch_size': 32, 'model__activation': 'relu', 'model__dropout_rate': 0.2, 'model__learning_rate': 0.001, 'model__momentum': 0.5, 'model__num_layers': 2, 'model__num_neurons': 32, 'model__reg_method': 'l1', 'model__reg_rate': 0.01}
0.808367 (0.024431) with: {'batch_size': 32, 'model__activation': 'relu', 'model__dropout_rate': 0.2, 'model__learning_rate': 0.001, 'model__momentum': 0.5, 'model__num_layers': 2, 'model__num_neurons': 32, 'model__reg_method':

## iteration 2

going to stick w relu activation and no dropout (commented out in build function)

In [10]:
BINARY_CLASSIFICATION = True
BINARY_ENCODE_THRESHOLD = 4 # values greater than this will be encoded as 1

In [11]:
# Load dataset
X = data[features]

if BINARY_CLASSIFICATION:
    y = data['Depression_Score'].apply(lambda x: 1 if x > BINARY_ENCODE_THRESHOLD else 0)
else:
    y = data['Depression_Score']

# Split data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=12, shuffle=True)

# Preprocess data
scaler = MinMaxScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

# Define parameters grid for grid search
param_grid = {
    # parameters for Sequential model
    'model__num_layers': [2, 3, 4], # number of hidden layers
    'model__num_neurons': [8, 10, 12],
    # 'model__dropout_rate': [0.2, 0.5],
    'model__momentum': [0.5, 0.9],
    'model__activation': ['relu'],
    'model__reg_method': ['l1', 'l2'],
    'model__reg_rate': [0.001, 0.01],
    'model__learning_rate': [0.001, 0.01],
    # parameters for KerasClassifier
    'batch_size': [32, 64]
}

# Create KerasClassifier wrapper for scikit-learn
model = KerasClassifier(build_fn=build_model, epochs=10, verbose=1)

# Perform grid search with cross-validation
kfold = KFold(n_splits=5, shuffle=True, random_state=42)

grid_search = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=-1, cv=kfold, scoring='accuracy')
grid_result = grid_search.fit(X_train, y_train)

c:\repos\ECS171FQ24_ResearchProject_SATAK\.venv\Lib\site-packages\joblib\externals\loky\process_executor.py:752: UserWarning: A worker stopped while some jobs were given to the executor. This can be caused by a too short worker timeout or by a memory leak.
  warnings.warn(
c:\repos\ECS171FQ24_ResearchProject_SATAK\.venv\Lib\site-packages\numpy\ma\core.py:2846: RuntimeWarning: invalid value encountered in cast
  _data = np.array(data, dtype=dtype, copy=copy,
c:\repos\ECS171FQ24_ResearchProject_SATAK\.venv\Lib\site-packages\scikeras\wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)


Epoch 1/10
24/24 ━━━━━━━━━━━━━━━━━━━━ 1s 2ms/step - accuracy: 0.8121 - loss: 0.6751   
Epoch 2/10
24/24 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step - accuracy: 0.8398 - loss: 0.6589 
Epoch 3/10
24/24 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step - accuracy: 0.8630 - loss: 0.6398 
Epoch 4/10
24/24 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step - accuracy: 0.8899 - loss: 0.6216 
Epoch 5/10
24/24 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step - accuracy: 0.9076 - loss: 0.6018 
Epoch 6/10
24/24 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - accuracy: 0.9079 - loss: 0.5873 
Epoch 7/10
24/24 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - accuracy: 0.9076 - loss: 0.5724 
Epoch 8/10
24/24 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - accuracy: 0.9014 - loss: 0.5590 
Epoch 9/10
24/24 ━━━━━━━━━━━━━━━━━━━━ 0s 2ms/step - accuracy: 0.9127 - loss: 0.5441 
Epoch 10/10
24/24 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - accuracy: 0.9099 - loss: 0.5329 


In [12]:
# Print results
print("Best: %f using %s" % (grid_result.best_score_, grid_result.best_params_))
means = grid_result.cv_results_['mean_test_score']
stds = grid_result.cv_results_['std_test_score']
params = grid_result.cv_results_['params']
for mean, std, param in zip(means, stds, params):
    print("%f (%f) with: %r" % (mean, std, param))

Best: 0.911499 using {'batch_size': 32, 'model__activation': 'relu', 'model__learning_rate': 0.001, 'model__momentum': 0.5, 'model__num_layers': 2, 'model__num_neurons': 12, 'model__reg_method': 'l2', 'model__reg_rate': 0.001}
0.910157 (0.020720) with: {'batch_size': 32, 'model__activation': 'relu', 'model__learning_rate': 0.001, 'model__momentum': 0.5, 'model__num_layers': 2, 'model__num_neurons': 8, 'model__reg_method': 'l1', 'model__reg_rate': 0.001}
0.894157 (0.026677) with: {'batch_size': 32, 'model__activation': 'relu', 'model__learning_rate': 0.001, 'model__momentum': 0.5, 'model__num_layers': 2, 'model__num_neurons': 8, 'model__reg_method': 'l1', 'model__reg_rate': 0.01}
0.872582 (0.076356) with: {'batch_size': 32, 'model__activation': 'relu', 'model__learning_rate': 0.001, 'model__momentum': 0.5, 'model__num_layers': 2, 'model__num_neurons': 8, 'model__reg_method': 'l2', 'model__reg_rate': 0.001}
0.837673 (0.117275) with: {'batch_size': 32, 'model__activation': 'relu', 'model_

# Iteration 3

engineering dataset only

Threshold of 3, i.e. 4,5 marked depressed

In [11]:
BINARY_CLASSIFICATION = True
BINARY_ENCODE_THRESHOLD = 3 # values greater than this will be encoded as 1

In [12]:
# Load dataset
X = data[features]

if BINARY_CLASSIFICATION:
    y = data['Depression_Score'].apply(lambda x: 1 if x > BINARY_ENCODE_THRESHOLD else 0)
else:
    y = data['Depression_Score']

# Split data into training and testing sets
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=12, shuffle=True)

# Preprocess data
scaler = MinMaxScaler()
X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

# Define parameters grid for grid search
param_grid = {
    # parameters for Sequential model
    'model__num_layers': [2, 3, 4], # number of hidden layers
    'model__num_neurons': [8, 10, 12],
    # 'model__dropout_rate': [0.2, 0.5],
    'model__momentum': [0.5, 0.9],
    'model__activation': ['relu'],
    'model__reg_method': ['l1', 'l2'],
    'model__reg_rate': [0.001, 0.01],
    'model__learning_rate': [0.001, 0.01],
    # parameters for KerasClassifier
    'batch_size': [32, 64]
}

# Create KerasClassifier wrapper for scikit-learn
model = KerasClassifier(build_fn=build_model, epochs=10, verbose=1)

# Perform grid search with cross-validation
kfold = KFold(n_splits=5, shuffle=True, random_state=42)

grid_search = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=-1, cv=kfold, scoring='accuracy')
grid_result = grid_search.fit(X_train, y_train)

/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X,

Epoch 1/10
Epoch 1/10
Epoch 1/10
Epoch 1/10
Epoch 1/10
Epoch 1/10
Epoch 1/10
Epoch 1/10
Epoch 1/10
Epoch 1/10
Epoch 1/10
Epoch 1/10
19/19 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - accuracy: 0.3053 - loss: 1.0125   
Epoch 2/10
19/19 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - accuracy: 0.8256 - loss: 0.9307   
19/19 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - accuracy: 0.2862 - loss: 0.7387   
19/19 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - accuracy: 0.1545 - loss: 0.8620  
Epoch 2/10
Epoch 2/10
Epoch 2/10
19/19 ━━━━━━━━━━━━━━━━━━━━ 1s 3ms/step - accuracy: 0.2787 - loss: 0.8017   
19/19 ━━━━━━━━━━━━━━━━━━━━ 1s 3ms/step - accuracy: 0.6524 - loss: 0.9817   
Epoch 2/10
Epoch 2/10
19/19 ━━━━━━━━━━━━━━━━━━━━ 1s 3ms/step - accuracy: 0.7771 - loss: 0.6445   
Epoch 2/10
19/19 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - accuracy: 0.4237 - loss: 1.0031 
Epoch 3/10
19/19 ━━━━━━━━━━━━━━━━━━━━ 1s 3ms/step - accuracy: 0.2671 - loss: 1.0428   
Epoch 2/10
19/19 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - accuracy: 0.8207 - loss: 0.9245 
Epoch 3/10
19/

/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X,

5/5 ━━━━━━━━━━━━━━━━━━━━ 0s 6ms/step 
5/5 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step 
5/5 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step 
Epoch 1/10
5/5 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step
Epoch 1/10
Epoch 1/10
5/5 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step 
5/5 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step
5/5 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
Epoch 1/10
1/5 ━━━━━━━━━━━━━━━━━━━━ 0s 35ms/stepEpoch 1/10
Epoch 1/10
Epoch 1/10
Epoch 1/10
5/5 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step
Epoch 1/10
Epoch 1/10
19/19 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - accuracy: 0.2425 - loss: 0.7584  
Epoch 2/10
 1/19 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step - accuracy: 0.2812 - loss: 0.7542Epoch 1/10
19/19 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - accuracy: 0.2676 - loss: 0.7527 
Epoch 3/10
19/19 ━━━━━━━━━━━━━━━━━━━━ 1s 6ms/step - accuracy: 0.7462 - loss: 0.7983 57
Epoch 2/10
19/19 ━━━━━━━━━━━━━━━━━━━━ 1s 6ms/step - accuracy: 0.8161 - loss: 0.5275 
Epoch 2/10
19/19 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.3254 - loss: 0.7451
Epoch 4/10
19/19 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step

/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X,

...

10/10 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.8195 - loss: 1.6214 
Epoch 6/10
10/10 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.8232 - loss: 0.5023 
Epoch 6/10
10/10 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - accuracy: 0.8126 - loss: 1.6033
Epoch 6/10
Epoch 1/10
10/10 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - accuracy: 0.8100 - loss: 1.31183
10/10 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.7931 - loss: 1.6058 
Epoch 7/10
10/10 ━━━━━━━━━━━━━━━━━━━━ 1s 6ms/step - accuracy: 0.2918 - loss: 0.7559  
Epoch 2/10
10/10 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.7838 - loss: 0.5618 
Epoch 7/10
10/10 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.8164 - loss: 1.5502 
Epoch 7/10
10/10 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - accuracy: 0.2928 - loss: 0.7637  
Epoch 2/10
 1/10 ━━━━━━━━━━━━━━━━━━━━ 0s 17ms/step - accuracy: 0.7969 - loss: 1.5462Epoch 1/10
10/10 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.7924 - loss: 1.5639 
Epoch 8/10
10/10 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.8350 - los

/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)


10/10 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.8112 - loss: 0.5368 
Epoch 7/10
10/10 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.8024 - loss: 1.7054 
Epoch 4/10
10/10 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.8302 - loss: 0.5150 
Epoch 8/10
3/3 ━━━━━━━━━━━━━━━━━━━━ 0s 26ms/stepep - accuracy: 0.8750 - loss: 1.5726
10/10 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - accuracy: 0.6888 - loss: 0.7134
Epoch 2/10
10/10 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.7818 - loss: 0.5677 
Epoch 8/10
10/10 ━━━━━━━━━━━━━━━━━━━━ 0s 4ms/step - accuracy: 0.8150 - loss: 0.5261 
Epoch 9/10
10/10 ━━━━━━━━━━━━━━━━━━━━ 0s 5ms/step - accuracy: 0.8148 - loss: 1.6137 
Epoch 5/10
10/10 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - accuracy: 0.7928 - loss: 0.6103 4
Epoch 3/10
3/3 ━━━━━━━━━━━━━━━━━━━━ 0s 28ms/step
10/10 ━━━━━━━━━━━━━━━━━━━━ 0s 3ms/step - accuracy: 0.8137 - loss: 0.5247 
Epoch 10/10
10/10 ━━━━━━━━━━━━━━━━━━━━ 1s 4ms/step - accuracy: 0.8112 - loss: 0.6960  
Epoch 2/10
3/3 ━━━━━━━━━━━━━━━━━━━━ 0s 31ms/ste

/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)


12/12 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step - accuracy: 0.8114 - loss: 0.9387  
Epoch 2/10
12/12 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step - accuracy: 0.7965 - loss: 0.9243 
Epoch 3/10
12/12 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step - accuracy: 0.8072 - loss: 0.8930
Epoch 4/10
12/12 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step - accuracy: 0.8146 - loss: 0.8665
Epoch 5/10
12/12 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step - accuracy: 0.8102 - loss: 0.8462
Epoch 6/10
12/12 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step - accuracy: 0.8013 - loss: 0.8440
Epoch 7/10
12/12 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step - accuracy: 0.8068 - loss: 0.8324
Epoch 8/10
12/12 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step - accuracy: 0.8152 - loss: 0.8184
Epoch 9/10
12/12 ━━━━━━━━━━━━━━━━━━━━ 0s 992us/step - accuracy: 0.8237 - loss: 0.8036
Epoch 10/10
12/12 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step - accuracy: 0.7882 - loss: 0.8447


In [13]:
# Print results
print("Best: %f using %s" % (grid_result.best_score_, grid_result.best_params_))
means = grid_result.cv_results_['mean_test_score']
stds = grid_result.cv_results_['std_test_score']
params = grid_result.cv_results_['params']
for mean, std, param in zip(means, stds, params):
    print("%f (%f) with: %r" % (mean, std, param))

Best: 0.809709 using {'batch_size': 64, 'model__activation': 'relu', 'model__learning_rate': 0.001, 'model__momentum': 0.9, 'model__num_layers': 4, 'model__num_neurons': 8, 'model__reg_method': 'l2', 'model__reg_rate': 0.01}
0.734541 (0.154374) with: {'batch_size': 32, 'model__activation': 'relu', 'model__learning_rate': 0.001, 'model__momentum': 0.5, 'model__num_layers': 2, 'model__num_neurons': 8, 'model__reg_method': 'l1', 'model__reg_rate': 0.001}
0.805682 (0.021486) with: {'batch_size': 32, 'model__activation': 'relu', 'model__learning_rate': 0.001, 'model__momentum': 0.5, 'model__num_layers': 2, 'model__num_neurons': 8, 'model__reg_method': 'l1', 'model__reg_rate': 0.01}
0.783034 (0.072642) with: {'batch_size': 32, 'model__activation': 'relu', 'model__learning_rate': 0.001, 'model__momentum': 0.5, 'model__num_layers': 2, 'model__num_neurons': 8, 'model__reg_method': 'l2', 'model__reg_rate': 0.001}
0.728367 (0.181298) with: {'batch_size': 32, 'model__activation': 'relu', 'model__l

# Iteration 4

Per major datasets for threshold of 3

In [23]:
import warnings
warnings.filterwarnings('ignore')
import os
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3' 

BINARY_CLASSIFICATION = True
BINARY_ENCODE_THRESHOLD = 3 # values greater than this will be encoded as 1

# features = ['Age', 'CGPA', 'Semester_Credit_Load', 'Anxiety_Score']
majors = ['business','compsci','engineering','law','medical','others']
grid_search_dict={}

for major in majors:
    print("For Major: ", major)
    data = pd.read_csv(f'../Data/clean_df_{major}.csv')
    data.drop(['Course'], axis=1, inplace=True)

    # Load dataset
    X = data[features]

    if BINARY_CLASSIFICATION:
        y = data['Depression_Score'].apply(lambda x: 1 if x > BINARY_ENCODE_THRESHOLD else 0)
    else:
        y = data['Depression_Score']

    # Split data into training and testing sets
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=12, shuffle=True)

    # Preprocess data
    scaler = MinMaxScaler()
    X_train = scaler.fit_transform(X_train)
    X_test = scaler.transform(X_test)

    # Define parameters grid for grid search
    param_grid = {
        # parameters for Sequential model
        'model__num_layers': [2, 3, 4], # number of hidden layers
        'model__num_neurons': [8, 10, 12],
        # 'model__dropout_rate': [0.2, 0.5],
        'model__momentum': [0.5, 0.9],
        'model__activation': ['relu'],
        'model__reg_method': ['l1', 'l2'],
        'model__reg_rate': [0.001, 0.01],
        'model__learning_rate': [0.001, 0.01],
        # parameters for KerasClassifier
        'batch_size': [32, 64]
    }

    # Create KerasClassifier wrapper for scikit-learn
    model = KerasClassifier(build_fn=build_model, epochs=10, verbose=0)

    # Perform grid search with cross-validation
    kfold = KFold(n_splits=5, shuffle=True, random_state=42)

    grid_search = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=-1, cv=kfold, scoring='accuracy')
    grid_result = grid_search.fit(X_train, y_train)
    grid_search_dict[major]= grid_result
    # Print results
    print("For Major: ",major,", Best: %f using %s" % (grid_result.best_score_, grid_result.best_params_))


For Major:  business


/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X,

For Major:  business , Best: 0.802000 using {'batch_size': 32, 'model__activation': 'relu', 'model__learning_rate': 0.001, 'model__momentum': 0.9, 'model__num_layers': 2, 'model__num_neurons': 8, 'model__reg_method': 'l1', 'model__reg_rate': 0.01}
For Major:  compsci


/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X,

For Major:  compsci , Best: 0.555245 using {'batch_size': 32, 'model__activation': 'relu', 'model__learning_rate': 0.001, 'model__momentum': 0.5, 'model__num_layers': 3, 'model__num_neurons': 12, 'model__reg_method': 'l1', 'model__reg_rate': 0.001}
For Major:  engineering


...

For Major:  law , Best: 0.802297 using {'batch_size': 32, 'model__activation': 'relu', 'model__learning_rate': 0.001, 'model__momentum': 0.5, 'model__num_layers': 4, 'model__num_neurons': 10, 'model__reg_method': 'l2', 'model__reg_rate': 0.001}
For Major:  medical


/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X,

For Major:  medical , Best: 0.808449 using {'batch_size': 32, 'model__activation': 'relu', 'model__learning_rate': 0.001, 'model__momentum': 0.5, 'model__num_layers': 3, 'model__num_neurons': 10, 'model__reg_method': 'l2', 'model__reg_rate': 0.001}
For Major:  others


/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X,

For Major:  others , Best: 0.787515 using {'batch_size': 32, 'model__activation': 'relu', 'model__learning_rate': 0.001, 'model__momentum': 0.5, 'model__num_layers': 2, 'model__num_neurons': 8, 'model__reg_method': 'l2', 'model__reg_rate': 0.001}


In [24]:
for major in majors:
    result = grid_search_dict[major]
    print("For Major: ", major, ", Best: %f using %s" % (result.best_score_, result.best_params_))


For Major:  business , Best: 0.802000 using {'batch_size': 32, 'model__activation': 'relu', 'model__learning_rate': 0.001, 'model__momentum': 0.9, 'model__num_layers': 2, 'model__num_neurons': 8, 'model__reg_method': 'l1', 'model__reg_rate': 0.01}
For Major:  compsci , Best: 0.555245 using {'batch_size': 32, 'model__activation': 'relu', 'model__learning_rate': 0.001, 'model__momentum': 0.5, 'model__num_layers': 3, 'model__num_neurons': 12, 'model__reg_method': 'l1', 'model__reg_rate': 0.001}
For Major:  engineering , Best: 0.809709 using {'batch_size': 64, 'model__activation': 'relu', 'model__learning_rate': 0.001, 'model__momentum': 0.5, 'model__num_layers': 4, 'model__num_neurons': 12, 'model__reg_method': 'l2', 'model__reg_rate': 0.001}
For Major:  law , Best: 0.802297 using {'batch_size': 32, 'model__activation': 'relu', 'model__learning_rate': 0.001, 'model__momentum': 0.5, 'model__num_layers': 4, 'model__num_neurons': 10, 'model__reg_method': 'l2', 'model__reg_rate': 0.001}
For M

# Iteration 5

Per major datasets for threshold of 4

In [ ]:
import warnings
warnings.filterwarnings('ignore')
import os
os.environ['TF_CPP_MIN_LOG_LEVEL'] = '3' 

BINARY_CLASSIFICATION = True
BINARY_ENCODE_THRESHOLD = 4 # values greater than this will be encoded as 1

# features = ['Age', 'CGPA', 'Semester_Credit_Load', 'Anxiety_Score']
majors = ['business','compsci','engineering','law','medical','others']
grid_search_dict={}

for major in majors:
    print("For Major: ", major)
    data = pd.read_csv(f'../Data/clean_df_{major}.csv')
    data.drop(['Course'], axis=1, inplace=True)

    # Load dataset
    X = data[features]

    if BINARY_CLASSIFICATION:
        y = data['Depression_Score'].apply(lambda x: 1 if x > BINARY_ENCODE_THRESHOLD else 0)
    else:
        y = data['Depression_Score']

    # Split data into training and testing sets
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=12, shuffle=True)

    # Preprocess data
    scaler = MinMaxScaler()
    X_train = scaler.fit_transform(X_train)
    X_test = scaler.transform(X_test)

    # Define parameters grid for grid search
    param_grid = {
        # parameters for Sequential model
        'model__num_layers': [2, 3, 4], # number of hidden layers
        'model__num_neurons': [8, 10, 12],
        # 'model__dropout_rate': [0.2, 0.5],
        'model__momentum': [0.5, 0.9],
        'model__activation': ['relu'],
        'model__reg_method': ['l1', 'l2'],
        'model__reg_rate': [0.001, 0.01],
        'model__learning_rate': [0.001, 0.01],
        # parameters for KerasClassifier
        'batch_size': [32, 64]
    }

    # Create KerasClassifier wrapper for scikit-learn
    model = KerasClassifier(build_fn=build_model, epochs=10, verbose=0)

    # Perform grid search with cross-validation
    kfold = KFold(n_splits=5, shuffle=True, random_state=42)

    grid_search = GridSearchCV(estimator=model, param_grid=param_grid, n_jobs=-1, cv=kfold, scoring='accuracy')
    grid_result = grid_search.fit(X_train, y_train)
    grid_search_dict[major]= grid_result
    # Print results
    print("For Major: ",major,", Best: %f using %s" % (grid_result.best_score_, grid_result.best_params_))


For Major:  business


/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X,

For Major:  business , Best: 0.888000 using {'batch_size': 32, 'model__activation': 'relu', 'model__learning_rate': 0.001, 'model__momentum': 0.5, 'model__num_layers': 2, 'model__num_neurons': 8, 'model__reg_method': 'l1', 'model__reg_rate': 0.01}
For Major:  compsci


/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X,

For Major:  compsci , Best: 0.765035 using {'batch_size': 32, 'model__activation': 'relu', 'model__learning_rate': 0.001, 'model__momentum': 0.5, 'model__num_layers': 2, 'model__num_neurons': 12, 'model__reg_method': 'l2', 'model__reg_rate': 0.001}
For Major:  engineering


...

For Major:  law , Best: 0.900625 using {'batch_size': 32, 'model__activation': 'relu', 'model__learning_rate': 0.001, 'model__momentum': 0.5, 'model__num_layers': 2, 'model__num_neurons': 8, 'model__reg_method': 'l1', 'model__reg_rate': 0.001}
For Major:  medical


/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X,

For Major:  medical , Best: 0.909350 using {'batch_size': 64, 'model__activation': 'relu', 'model__learning_rate': 0.001, 'model__momentum': 0.5, 'model__num_layers': 3, 'model__num_neurons': 10, 'model__reg_method': 'l1', 'model__reg_rate': 0.001}
For Major:  others


/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X, y = self._initialize(X, y)
/opt/anaconda3/envs/tf2.10_env/lib/python3.9/site-packages/scikeras/wrappers.py:925: UserWarning: ``build_fn`` will be renamed to ``model`` in a future release, at which point use of ``build_fn`` will raise an Error instead.
  X,

For Major:  others , Best: 0.897737 using {'batch_size': 32, 'model__activation': 'relu', 'model__learning_rate': 0.001, 'model__momentum': 0.5, 'model__num_layers': 3, 'model__num_neurons': 12, 'model__reg_method': 'l1', 'model__reg_rate': 0.01}


In [29]:
print("For Threshold of",BINARY_ENCODE_THRESHOLD)
for major in majors:
    result = grid_search_dict[major]
    print("For", major, ", Best: %f using %s" % (result.best_score_, result.best_params_))


For Threshold of 4
For business , Best: 0.888000 using {'batch_size': 32, 'model__activation': 'relu', 'model__learning_rate': 0.001, 'model__momentum': 0.5, 'model__num_layers': 2, 'model__num_neurons': 8, 'model__reg_method': 'l1', 'model__reg_rate': 0.01}
For compsci , Best: 0.765035 using {'batch_size': 32, 'model__activation': 'relu', 'model__learning_rate': 0.001, 'model__momentum': 0.5, 'model__num_layers': 2, 'model__num_neurons': 12, 'model__reg_method': 'l2', 'model__reg_rate': 0.001}
For engineering , Best: 0.910157 using {'batch_size': 32, 'model__activation': 'relu', 'model__learning_rate': 0.001, 'model__momentum': 0.5, 'model__num_layers': 2, 'model__num_neurons': 12, 'model__reg_method': 'l2', 'model__reg_rate': 0.001}
For law , Best: 0.900625 using {'batch_size': 32, 'model__activation': 'relu', 'model__learning_rate': 0.001, 'model__momentum': 0.5, 'model__num_layers': 2, 'model__num_neurons': 8, 'model__reg_method': 'l1', 'model__reg_rate': 0.001}
For medical , Best: